In [ ]:
!pip -q install --upgrade lerobot torch torchvision timm imageio[ffmpeg]

import os, math, random, io, sys, json, pathlib, time
import torch, torch.nn as nn, torch.nn.functional as F
from torch.utils.data import DataLoader, Subset
from torchvision.utils import make_grid, save_image
import numpy as np
import imageio.v2 as imageio

try:
    from lerobot.common.datasets.lerobot_dataset import LeRobotDataset
except Exception:
    from lerobot.datasets.lerobot_dataset import LeRobotDataset

DEVICE = "cuda" if torch.cuda.is_available() else "cpu"
SEED = 42
random.seed(SEED); np.random.seed(SEED); torch.manual_seed(SEED)

In [ ]:
REPO_ID = "lerobot/pusht"
ds = LeRobotDataset(REPO_ID)
print("Dataset length:", len(ds))

s0 = ds[0]
keys = list(s0.keys())
print("Sample keys:", keys)

def key_with(prefixes):
    for k in keys:
        for p in prefixes:
            if k.startswith(p): return k
    return None

K_IMG = key_with(["observation.image", "observation.images", "observation.rgb"])
K_STATE = key_with(["observation.state"])
K_ACT = "action"
assert K_ACT in s0, f"No 'action' key found in sample. Found: {keys}"
print("Using keys -> IMG:", K_IMG, "STATE:", K_STATE, "ACT:", K_ACT)

In [ ]:
class PushTWrapper(torch.utils.data.Dataset):
    def __init__(self, base):
        self.base = base
    def __len__(self): return len(self.base)
    def __getitem__(self, i):
        x = self.base[i]
        img = x[K_IMG]
        if img.ndim == 4: img = img[-1]
        img = img.float() / 255.0 if img.dtype==torch.uint8 else img.float()
        state = x.get(K_STATE, torch.zeros(2))
        state = state.float().reshape(-1)
        act = x[K_ACT].float().reshape(-1)
        if img.shape[-2:] != (96,96):
            img = F.interpolate(img.unsqueeze(0), size=(96,96), mode="bilinear", align_corners=False)[0]
        return {"image": img, "state": state, "action": act}

wrapped = PushTWrapper(ds)
N = len(wrapped)
idx = list(range(N))
random.shuffle(idx)
n_train = int(0.9*N)
train_idx, val_idx = idx[:n_train], idx[n_train:]

train_ds = Subset(wrapped, train_idx[:12000])
val_ds   = Subset(wrapped, val_idx[:2000])

BATCH = 128
train_loader = DataLoader(train_ds, batch_size=BATCH, shuffle=True, num_workers=2, pin_memory=True)
val_loader   = DataLoader(val_ds,   batch_size=BATCH, shuffle=False, num_workers=2, pin_memory=True)

In [ ]:
class SmallBackbone(nn.Module):
    def __init__(self, out=256):
        super().__init__()
        self.conv = nn.Sequential(
            nn.Conv2d(3, 32, 5, 2, 2), nn.ReLU(inplace=True),
            nn.Conv2d(32, 64, 3, 2, 1), nn.ReLU(inplace=True),
            nn.Conv2d(64,128, 3, 2, 1), nn.ReLU(inplace=True),
            nn.Conv2d(128,128,3, 1, 1), nn.ReLU(inplace=True),
        )
        self.head = nn.Sequential(nn.AdaptiveAvgPool2d(1), nn.Flatten(), nn.Linear(128, out), nn.ReLU(inplace=True))
    def forward(self, x): return self.head(self.conv(x))

class BCPolicy(nn.Module):
    def __init__(self, img_dim=256, state_dim=2, hidden=256, act_dim=2):
        super().__init__()
        self.backbone = SmallBackbone(img_dim)
        self.mlp = nn.Sequential(
            nn.Linear(img_dim + state_dim, hidden), nn.ReLU(inplace=True),
            nn.Linear(hidden, hidden//2), nn.ReLU(inplace=True),
            nn.Linear(hidden//2, act_dim)
        )
    def forward(self, img, state):
        z = self.backbone(img)
        if state.ndim==1: state = state.unsqueeze(0)
        z = torch.cat([z, state], dim=-1)
        return self.mlp(z)

policy = BCPolicy().to(DEVICE)
opt = torch.optim.AdamW(policy.parameters(), lr=3e-4, weight_decay=1e-4)
scaler = torch.cuda.amp.GradScaler(enabled=(DEVICE=="cuda"))

@torch.no_grad()
def evaluate():
    policy.eval()
    mse, n = 0.0, 0
    for batch in val_loader:
        img = batch["image"].to(DEVICE, non_blocking=True)
        st  = batch["state"].to(DEVICE, non_blocking=True)
        act = batch["action"].to(DEVICE, non_blocking=True)
        pred = policy(img, st)
        mse += F.mse_loss(pred, act, reduction="sum").item()
        n += act.numel()
    return mse / n

def cosine_lr(step, total, base=3e-4, min_lr=3e-5):
    if step>=total: return min_lr
    cos = 0.5*(1+math.cos(math.pi*step/total))
    return min_lr + (base-min_lr)*cos

EPOCHS = 4
steps_total = EPOCHS*len(train_loader)
step = 0
best = float("inf")
ckpt = "/content/lerobot_pusht_bc.pt"

for epoch in range(EPOCHS):
    policy.train()
    for batch in train_loader:
        lr = cosine_lr(step, steps_total); step += 1
        for g in opt.param_groups: g["lr"] = lr

        img = batch["image"].to(DEVICE, non_blocking=True)
        st  = batch["state"].to(DEVICE, non_blocking=True)
        act = batch["action"].to(DEVICE, non_blocking=True)

        opt.zero_grad(set_to_none=True)
        with torch.cuda.amp.autocast(enabled=(DEVICE=="cuda")):
            pred = policy(img, st)
            loss = F.smooth_l1_loss(pred, act)
        scaler.scale(loss).backward()
        nn.utils.clip_grad_norm_(policy.parameters(), 1.0)
        scaler.step(opt); scaler.update()

    val_mse = evaluate()
    print(f"Epoch {epoch+1}/{EPOCHS} | Val MSE: {val_mse:.6f}")
    if val_mse < best:
        best = val_mse
        torch.save({"state_dict": policy.state_dict(), "val_mse": best}, ckpt)

print("Best Val MSE:", best, "| Saved:", ckpt)

In [1]:
policy.load_state_dict(torch.load(ckpt)["state_dict"]); policy.eval()
os.makedirs("/content/vis", exist_ok=True)

def draw_arrow(imgCHW, action_xy, scale=40):
    import PIL.Image, PIL.ImageDraw
    C,H,W = imgCHW.shape
    arr = (imgCHW.clamp(0,1).permute(1,2,0).cpu().numpy()*255).astype(np.uint8)
    im = PIL.Image.fromarray(arr)
    dr = PIL.ImageDraw.Draw(im)
    cx, cy = W//2, H//2
    dx, dy = float(action_xy[0])*scale, float(-action_xy[1])*scale
    dr.line((cx, cy, cx+dx, cy+dy), width=3, fill=(0,255,0))
    return np.array(im)

frames = []
with torch.no_grad():
    for i in range(60):
        b = wrapped[i]
        img = b["image"].unsqueeze(0).to(DEVICE)
        st  = b["state"].unsqueeze(0).to(DEVICE)
        pred = policy(img, st)[0].cpu()
        frames.append(draw_arrow(b["image"], pred))
video_path = "/content/vis/pusht_pred.mp4"
imageio.mimsave(video_path, frames, fps=10)
print("Wrote", video_path)

grid = make_grid(torch.stack([wrapped[i]["image"] for i in range(16)]), nrow=8)
save_image(grid, "/content/vis/grid.png")
print("Saved grid:", "/content/vis/grid.png")

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 597.7/597.7 kB 21.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 71.8/71.8 kB 5.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 821.0/821.0 MB 1.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 571.0/571.0 MB 2.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 156.8/156.8 MB 8.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 201.3/201.3 MB 6.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 155.7/155.7 MB 6.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.5/7.5 MB 109.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 39.9/39.9 MB 18.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 491.5/491.5 kB 32.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 91.4/91.4 kB 7.0 MB/s et

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Fetching 4 files:   0%|          | 0/4 [00:00<?, ?it/s]

episodes.jsonl: 0.00B [00:00, ?B/s]

episodes_stats.jsonl: 0.00B [00:00, ?B/s]

...

Resolving data files:   0%|          | 0/206 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Dataset length: 25650
Sample keys: ['observation.image', 'observation.state', 'action', 'episode_index', 'frame_index', 'timestamp', 'next.reward', 'next.done', 'next.success', 'index', 'task_index', 'task']
Using keys -> IMG: observation.image STATE: observation.state ACT: action


/tmp/ipython-input-1661098065.py:114: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  scaler = torch.cuda.amp.GradScaler(enabled=(DEVICE=="cuda"))
/usr/local/lib/python3.12/dist-packages/torch/utils/data/dataloader.py:665: UserWarning: 'pin_memory' argument is set as true but no accelerator is found, then device pinned memory won't be used.
  warnings.warn(warn_msg)
/tmp/ipython-input-1661098065.py:151: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with torch.cuda.amp.autocast(enabled=(DEVICE=="cuda")):


Epoch 1/4 | Val MSE: 6358.897094
Epoch 2/4 | Val MSE: 1245.421395
Epoch 3/4 | Val MSE: 405.435186
Epoch 4/4 | Val MSE: 408.951506
Best Val MSE: 405.435185546875 | Saved: /content/lerobot_pusht_bc.pt
Wrote /content/vis/pusht_pred.mp4
Saved grid: /content/vis/grid.png
